# Configuration

In [1]:
# Import libraries
import pandas               as pd
import datetime             as dt
import numpy                as np
import os                   as os
import plotly.graph_objects as go
import requests             as requests

from PIL                   import Image
from datetime              import date
from datetime              import timedelta
from amberdata_derivatives import AmberdataDerivatives

# Load environment variables
from dotenv import load_dotenv
load_dotenv()

# Retrieve API key from .env file
API_KEY = os.getenv('API_KEY')

# Amberdata Logo
AMBERDATA_LOGO = Image.open("amberdata_logo_bug_color_100p.png")

# Amberdata SDK

In [2]:
# Create SDK client
amberdata_client = AmberdataDerivatives(api_key=API_KEY)

# Headers for REST calls
headers = {
    "accept"          : "application/json",
    "Accept-Encoding" : "gzip",
    "x-api-key"       : API_KEY
}

# Helper Functions

In [3]:
def svi_raw(params, k):
    '''
    This function is the raw SVI formula.
    Return volatility (varianace squared)
    
    params: list of 5 SVI parameters
    k: list of log moneyness values to fit 
    '''    
    a, b, sigma, rho, m = params
    return np.sqrt(a + b * (rho * (k - m) + np.sqrt((k - m) ** 2 + sigma ** 2)))

def apply_svi(row):
    params = [row['sviA'], row['sviB'], row['sviSigma'], row['sviRho'], row['sviM']]
    k      = row['moneyness']
    return svi_raw(params, k) * 100

In [4]:
def fecth_svi(exchange, currency):
    try:
        base_url = "https://api.amberdata.com"
        endpoint = f"/markets/derivatives/analytics/volatility/svi-historical?currency={currency}&exchange={exchange}&timeInterval=minute"
        url      = f"{base_url}{endpoint}"
        response = requests.get(url, headers=headers)
        response.raise_for_status() 

        data = response.json()
        svi  = pd.json_normalize(data['payload']['data'])

        svi['timestamp'] = pd.to_datetime(svi['timestamp'], unit='ms')
        svi['atmIv']     = svi_raw([svi['sviA'], svi['sviB'], svi['sviSigma'], svi['sviRho'], svi['sviM']], 0) * 100

        svi.sort_values('timestamp', ascending=False, inplace=True)

        return svi
    except requests.RequestException as e:
        print (f"Erorr: {e}")

In [5]:
def fetch_level_1_quotes(exchange, currency, hours_ago):
    svi_timestamp_last     =  pd.to_datetime(svi_ts['timestamp'].unique()[0]).strftime('%Y-%m-%dT%H:%M:%S.%f')
    svi_timestamp_last_end = (pd.to_datetime(svi_ts['timestamp'].unique()[0]) + timedelta(minutes=1)).strftime('%Y-%m-%dT%H:%M:%S')

    data = amberdata_client.get_volatility_level_1_quotes(
        exchange  = exchange,
        currency  = currency,
        startDate = svi_timestamp_last,
        endDate   = svi_timestamp_last_end
    )

    quotes                            = pd.json_normalize(data['payload']['data'])
    quotes['timestamp']               = pd.to_datetime(quotes['timestamp']          ).dt.tz_localize(None)
    quotes['expirationTimestamp']     = pd.to_datetime(quotes['expirationTimestamp']).dt.tz_localize(None)
    quotes['expirationTimestampDate'] = pd.to_datetime(quotes['expirationTimestamp'].dt.date).dt.tz_localize(None)

    quotes.loc[(quotes['strike'] <  quotes['underlyingPrice']) & (quotes['putCall'] == 'P'), 'moneyness'] = 'OTM'
    quotes.loc[(quotes['strike'] >= quotes['underlyingPrice']) & (quotes['putCall'] == 'P'), 'moneyness'] = 'ITM'
    quotes.loc[(quotes['strike'] <  quotes['underlyingPrice']) & (quotes['putCall'] == 'C'), 'moneyness'] = 'ITM'
    quotes.loc[(quotes['strike'] >= quotes['underlyingPrice']) & (quotes['putCall'] == 'C'), 'moneyness'] = 'OTM'

    return quotes[quotes['moneyness']=='OTM']

In [6]:
def generate_equidistant_strikes(quotes, step_size, timestamp_column='expirationTimestamp_quotes'):
    df = pd.DataFrame()

    for expiration in quotes[timestamp_column].unique():
        quotes_at_expiry = quotes[quotes[timestamp_column] == expiration]
        strikes          = quotes_at_expiry.sort_values('strike')['strike'].unique()

        # Define the minimum and maximum strikes
        strike_min = min(strikes)
        strike_max = max(strikes)

        # Generate equidistant strikes using np.arange()
        new_strikes = np.arange(strike_min, strike_max + step_size, step_size) # Add step_size to include max

        # Create the DataFrame for the generated strikes
        df_strikes = pd.DataFrame(new_strikes, columns=['strike'])
        df_strikes['expirationTimestamp'] = expiration

        # Concatenate the results to the final DataFrame
        df = pd.concat([df, df_strikes])

    return df

# Retrieve SVI

In [7]:
currency = 'BTC'
exchange = 'deribit'

In [8]:
svi                        = fecth_svi(exchange, currency)
svi['timestamp']           = pd.to_datetime(svi['timestamp'], unit='ms')
svi['expirationTimestamp'] = pd.to_datetime(svi['expirationTimestamp']).dt.tz_localize(None)
svi['underlyingPrice']     = svi['indexPrice'] + svi['forwardDifference']
svi.sort_values('timestamp', ascending=False, inplace=True)

svi_ts = svi[svi['timestamp'] == svi['timestamp'].max()-timedelta(hours=0)]

svi_ts

currency  daysToExpiration expirationTimestamp  forwardDifference  \
0      BTC              1.15          2024-11-20          78.750000   
3      BTC             10.15          2024-11-29         524.726562   
4      BTC             17.15          2024-12-06         789.742188   
5      BTC             38.15          2024-12-27        1578.859375   
6      BTC             73.15          2025-01-31        2720.132812   
7      BTC            129.15          2025-03-28        4545.453125   
8      BTC            220.15          2025-06-27        7380.398438   
9      BTC            311.15          2025-09-26        9875.718750   
1      BTC              2.15          2024-11-21         146.289062   
2      BTC              3.15          2024-11-22         213.781250   

   indexPrice      sviA       sviB      sviM    sviRho  sviSigma  \
0    91679.25 -0.264574  10.533835 -0.084202 -0.632978  0.075001   
3    91679.25 -0.273788   2.932563 -0.162727 -0.456693  0.239237   
4    91679.25 -0.773753   3.742317 -0.362813 -0.634066  0.384043   
5    91679.25 -1.596499   2.137915 -0.199910 -0.210022  0.919673   
6    91679.25 -0.041563   0.883109 -0.344856 -0.481981  0.461190   
7    91679.25 -0.342629   0.794598 -0.352069 -0.312127  0.861210   
8    91679.25 -0.180504   0.508511 -0.378318 -0.285093  1.007548   
9    91679.25  0.148584   0.284464 -0.420479 -0.376644  0.598647   
1    91679.25 -0.952219  10.630122 -0.141942 -0.605326  0.156127   
2    91679.25 -0.639164   6.794318 -0.132401 -0.509359  0.173729   

            timestamp      atmIv  underlyingPrice  
0 2024-11-19 04:30:00  60.150251     91758.000000  
3 2024-11-19 04:30:00  59.729983     92203.976562  
4 2024-11-19 04:30:00  58.521714     92468.992188  
5 2024-11-19 04:30:00  57.082270     93258.109375  
6 2024-11-19 04:30:00  56.586644     94399.382812  
7 2024-11-19 04:30:00  55.618579     96224.703125  
8 2024-11-19 04:30:00  55.850369     99059.648438  
9 2024-11-19 04:30:00  55.824397    101554.968750  
1 2024-11-19 04:30:00  61.435842     91825.539062  
2 2024-11-19 04:30:00  62.186208     91893.031250

# Retrieve Level-1-Quotes

In [9]:
quotes         = fetch_level_1_quotes(exchange, currency, hours_ago=0)
quotes_and_svi = quotes.merge(svi_ts, left_on='expirationTimestampDate', right_on='expirationTimestamp', suffixes=('_quotes','_svi'))

quotes_and_svi

ask   askIv  askVolume     bid  bidIv  bidVolume currency_quotes  \
0    0.0003  114.88       11.1  0.0000   0.00        0.0             BTC   
1    0.0002   96.47        5.0  0.0000   0.00        0.0             BTC   
2    0.0002   83.40        1.0  0.0001  76.53        2.9             BTC   
3    0.0004   77.33        0.1  0.0003  73.98        2.9             BTC   
4    0.0011   75.11        5.4  0.0007  68.51       17.5             BTC   
..      ...     ...        ...     ...    ...        ...             ...   
405  0.0265   59.71        6.6  0.0240  57.90       20.6             BTC   
406  0.0195   61.33        2.1  0.0175  59.53       22.8             BTC   
407  0.0110   67.23       33.5  0.0095  65.05        0.1             BTC   
408  0.0055   74.60       41.0  0.0040  70.43       37.1             BTC   
409  0.0021   83.85        6.1  0.0013  78.32       54.7             BTC   

       delta exchange         exchangeTimestamp  ... forwardDifference  \
0    0.00346  deribit  2024-11-19T04:30:00.748Z  ...          78.75000   
1    0.00612  deribit  2024-11-19T04:30:03.769Z  ...          78.75000   
2    0.00876  deribit  2024-11-19T04:30:04.776Z  ...          78.75000   
3    0.02050  deribit  2024-11-19T04:30:05.783Z  ...          78.75000   
4    0.04961  deribit  2024-11-19T04:30:00.748Z  ...          78.75000   
..       ...      ...                       ...  ...               ...   
405 -0.08035  deribit  2024-11-19T04:30:00.789Z  ...        9875.71875   
406 -0.06063  deribit  2024-11-19T04:30:00.789Z  ...        9875.71875   
407 -0.03289  deribit  2024-11-19T04:30:00.789Z  ...        9875.71875   
408 -0.01546  deribit  2024-11-19T04:30:00.789Z  ...        9875.71875   
409 -0.00544  deribit  2024-11-19T04:30:00.789Z  ...        9875.71875   

     indexPrice_svi      sviA       sviB      sviM    sviRho  sviSigma  \
0          91679.25 -0.264574  10.533835 -0.084202 -0.632978  0.075001   
1          91679.25 -0.264574  10.533835 -0.084202 -0.632978  0.075001   
2          91679.25 -0.264574  10.533835 -0.084202 -0.632978  0.075001   
3          91679.25 -0.264574  10.533835 -0.084202 -0.632978  0.075001   
4          91679.25 -0.264574  10.533835 -0.084202 -0.632978  0.075001   
..              ...       ...        ...       ...       ...       ...   
405        91679.25  0.148584   0.284464 -0.420479 -0.376644  0.598647   
406        91679.25  0.148584   0.284464 -0.420479 -0.376644  0.598647   
407        91679.25  0.148584   0.284464 -0.420479 -0.376644  0.598647   
408        91679.25  0.148584   0.284464 -0.420479 -0.376644  0.598647   
409        91679.25  0.148584   0.284464 -0.420479 -0.376644  0.598647   

          timestamp_svi      atmIv  underlyingPrice_svi  
0   2024-11-19 04:30:00  60.150251          91758.00000  
1   2024-11-19 04:30:00  60.150251          91758.00000  
2   2024-11-19 04:30:00  60.150251          91758.00000  
3   2024-11-19 04:30:00  60.150251          91758.00000  
4   2024-11-19 04:30:00  60.150251          91758.00000  
..                  ...        ...                  ...  
405 2024-11-19 04:30:00  55.824397         101554.96875  
406 2024-11-19 04:30:00  55.824397         101554.96875  
407 2024-11-19 04:30:00  55.824397         101554.96875  
408 2024-11-19 04:30:00  55.824397         101554.96875  
409 2024-11-19 04:30:00  55.824397         101554.96875  

[410 rows x 47 columns]

# Generate Strikes

In [10]:
strikes = generate_equidistant_strikes(quotes_and_svi, step_size=50)
strikes

strike expirationTimestamp
0      80000 2024-11-20 08:00:00
1      80050 2024-11-20 08:00:00
2      80100 2024-11-20 08:00:00
3      80150 2024-11-20 08:00:00
4      80200 2024-11-20 08:00:00
...      ...                 ...
5196  279800 2025-09-26 08:00:00
5197  279850 2025-09-26 08:00:00
5198  279900 2025-09-26 08:00:00
5199  279950 2025-09-26 08:00:00
5200  280000 2025-09-26 08:00:00

[30930 rows x 2 columns]

# Generate Curves

In [11]:
curves = strikes.merge(quotes_and_svi, left_on=['strike','expirationTimestamp'], right_on=['strike','expirationTimestamp_quotes'],how='left').ffill()    

curves['moneyness'] = np.log(curves['strike'] / curves['underlyingPrice_svi'])
curves['sviIv']     = curves.apply(apply_svi, axis=1)

curves

strike expirationTimestamp     ask   askIv  askVolume     bid  bidIv  \
0       80000 2024-11-20 08:00:00  0.0003  112.05       10.0  0.0001  97.59   
1       80050 2024-11-20 08:00:00  0.0003  112.05       10.0  0.0001  97.59   
2       80100 2024-11-20 08:00:00  0.0003  112.05       10.0  0.0001  97.59   
3       80150 2024-11-20 08:00:00  0.0003  112.05       10.0  0.0001  97.59   
4       80200 2024-11-20 08:00:00  0.0003  112.05       10.0  0.0001  97.59   
...       ...                 ...     ...     ...        ...     ...    ...   
30925  279800 2025-09-26 08:00:00  0.0255   66.26       14.7  0.0225  64.47   
30926  279850 2025-09-26 08:00:00  0.0255   66.26       14.7  0.0225  64.47   
30927  279900 2025-09-26 08:00:00  0.0255   66.26       14.7  0.0225  64.47   
30928  279950 2025-09-26 08:00:00  0.0255   66.26       14.7  0.0225  64.47   
30929  280000 2025-09-26 08:00:00  0.0220   67.66       17.3  0.0190  65.66   

       bidVolume currency_quotes    delta  ... indexPrice_svi      sviA  \
0            3.9             BTC -0.00811  ...       91679.25 -0.264574   
1            3.9             BTC -0.00811  ...       91679.25 -0.264574   
2            3.9             BTC -0.00811  ...       91679.25 -0.264574   
3            3.9             BTC -0.00811  ...       91679.25 -0.264574   
4            3.9             BTC -0.00811  ...       91679.25 -0.264574   
...          ...             ...      ...  ...            ...       ...   
30925       11.9             BTC  0.10498  ...       91679.25  0.148584   
30926       11.9             BTC  0.10498  ...       91679.25  0.148584   
30927       11.9             BTC  0.10498  ...       91679.25  0.148584   
30928       11.9             BTC  0.10498  ...       91679.25  0.148584   
30929       14.9             BTC  0.09047  ...       91679.25  0.148584   

            sviB      sviM    sviRho  sviSigma       timestamp_svi      atmIv  \
0      10.533835 -0.084202 -0.632978  0.075001 2024-11-19 04:30:00  60.150251   
1      10.533835 -0.084202 -0.632978  0.075001 2024-11-19 04:30:00  60.150251   
2      10.533835 -0.084202 -0.632978  0.075001 2024-11-19 04:30:00  60.150251   
3      10.533835 -0.084202 -0.632978  0.075001 2024-11-19 04:30:00  60.150251   
4      10.533835 -0.084202 -0.632978  0.075001 2024-11-19 04:30:00  60.150251   
...          ...       ...       ...       ...                 ...        ...   
30925   0.284464 -0.420479 -0.376644  0.598647 2024-11-19 04:30:00  55.824397   
30926   0.284464 -0.420479 -0.376644  0.598647 2024-11-19 04:30:00  55.824397   
30927   0.284464 -0.420479 -0.376644  0.598647 2024-11-19 04:30:00  55.824397   
30928   0.284464 -0.420479 -0.376644  0.598647 2024-11-19 04:30:00  55.824397   
30929   0.284464 -0.420479 -0.376644  0.598647 2024-11-19 04:30:00  55.824397   

       underlyingPrice_svi       sviIv  
0              91758.00000  102.726497  
1              91758.00000  102.339025  
2              91758.00000  101.951807  
3              91758.00000  101.564859  
4              91758.00000  101.178200  
...                    ...         ...  
30925         101554.96875   66.104195  
30926         101554.96875   66.106295  
30927         101554.96875   66.108394  
30928         101554.96875   66.110494  
30929         101554.96875   66.112592  

[30930 rows x 49 columns]

# Plot Curves

In [16]:
import matplotlib.pyplot as plt

for exp in curves.expirationTimestamp.unique():
    try:
        fig = go.Figure()

        curves_at_expiry = curves[curves['expirationTimestamp'] == exp].sort_values('strike')
        quotes_at_expiry = quotes[quotes['expirationTimestamp'] == exp].sort_values('strike')
        bidIv            = quotes_at_expiry['bidIv']
        askIv            = quotes_at_expiry['askIv']

        fig.add_trace(go.Scatter(x=curves_at_expiry.strike, y=curves_at_expiry.sviIv, name="SVI current", legendrank=1, line=dict(color='green')))
        fig.add_trace(go.Scatter(x=quotes_at_expiry.strike, y=bidIv,                  name='bid',         legendrank=3, mode='markers', marker_symbol="x-thin", marker_color="grey", marker_line_width=1, visible='legendonly'))
        fig.add_trace(go.Scatter(x=quotes_at_expiry.strike, y=askIv,                  name='ask',         legendrank=4, mode='markers', marker_symbol="x-thin", marker_color="grey", marker_line_width=1, visible='legendonly'))

        fig.add_vline(
            x          = curves_at_expiry['underlyingPrice_svi'].values[0],
            line_dash  = 'dashdot',
            line_width = 2,
            line_color = "green"
        )

        curves_at_expiry.replace('C', 'call', inplace=True)
        curves_at_expiry.replace('P', 'put',  inplace=True)

        fig.add_annotation(
            text      = str(pd.to_datetime(curves_at_expiry.timestamp_quotes.values[0])),
            opacity   = 0.5,
            xref      = "paper",
            yref      = "paper",
            x         = 1,
            y         = 0.05,
            showarrow = False,
            font      = dict(color='green')
        )

        fig.update_layout(
            title       = currency + " " + str(exp)[0:10] + " $" + str(round(curves_at_expiry['underlyingPrice_svi'].values[0], 2)),
            title_x     = 0.50,
            xaxis_title = "",
            yaxis_title = "iv",
            legend      = dict(orientation="h", yanchor="bottom", y=-0.20, xanchor="center", x=0.5),
            template    = 'plotly_white'
        )

        fig.layout.images = [dict(
            source  = AMBERDATA_LOGO,
            xref    = "paper",
            yref    = "paper",
            x       = 0.96,
            y       = 1.05,
            sizex   = 0.13,
            sizey   = 0.13,
            xanchor = "center",
            yanchor = "bottom"
        )]

        fig.update_xaxes(showline=True, showgrid=True, tickmode='auto')

        fig.show()

    except Exception as e:
        print(f"Error: {e}")